In [1]:
import http.client
import json
from settings import API_KEY
import time
from pandas.io.json import json_normalize
import pandas as pd
import  csv
import ast

## Funções

In [2]:
def get_url_credits(movie_id, api_key):
    return("/3/movie/" + str(movie_id) + "/credits" + "?api_key=" + str(api_key))

def get_json(conn, url):
	payload = "{}"
	conn.request("GET", url, payload)
	res = conn.getresponse()
	data = res.read()
	return(json.loads(data.decode("    utf-8")))

In [3]:
def get_movie_credits(ids):
    
	conn = http.client.HTTPSConnection("api.themoviedb.org")    
	movie_credits_df = pd.DataFrame()
    
	for movie_id in ids:
		url = get_url_credits(movie_id, API_KEY)
		movie_data = get_json(conn, url)
        
        #mudei!
		if ('status_code' in movie_data):
			time.sleep(10)  
			movie_data = get_json(conn, url)
		#else:
		#	movie_data = get_json(conn, url)
        
		df = json_normalize(movie_data)
		movie_credits_df = movie_credits_df.append(df)

	return movie_credits_df

In [40]:
def get_cast(ids, movie_credits_df):

    movie_cast_df = pd.DataFrame()

    print(movie_credits_df['id'])
    for idx,movie_id in enumerate(movie_credits_df['id'],40):
    #for movie_id in ids_num:

        movie_item = pd.DataFrame()
        #print(movie_credits_df.head(90))
        print("movie_id: %s" % (movie_id))
        movie_item = movie_credits_df[movie_credits_df['id']==movie_id].reset_index()
        #print(movie_item.head(90))
        print("%s of %s" % (idx,len(ids)))

        #print(movie_item['cast'])
        
        for cast_id in movie_item['cast'][0]:
            cast_id.update({'movie_id': int(movie_id)})
            cast_id.pop('profile_path', None)
            movie_cast_df = movie_cast_df.append(cast_id, ignore_index=True)
    
    return movie_cast_df

## Testes

In [22]:
#with open('out_sample.csv', 'r') as f:
with open('out_all.csv', 'r') as f:    
    reader = csv.reader(f, skipinitialspace=True, delimiter=',')
    ids_list = list(reader)
    
ids = [item for sublist in ids_list for item in sublist]

In [23]:
len(ids)

147507

In [24]:
# Transformando ids em numérico
ids_num = list(map(int, ids))

In [25]:
start_time = time.time()
movie_credits_df = get_movie_credits(ids_num)
print("--- Movie Credits: %s seconds ---" % (time.time() - start_time))
print("")

--- Movie Credits: 66942.09025907516 seconds ---



In [26]:
movie_credits_df = movie_credits_df.reset_index().drop('index', axis=1)

In [28]:
movie_credits_df.shape

(147507, 5)

In [29]:
movie_credits_df.head()

cast  \
0  [{'character': 'Leonard', 'id': 529, 'cast_id'...   
1  [{'character': 'Maximus', 'id': 934, 'cast_id'...   
2  [{'character': 'Patrick Bateman', 'id': 3894, ...   
3  [{'character': 'Chuck Noland', 'id': 31, 'cast...   
4  [{'character': 'Rocky (Voice)', 'id': 2461, 'c...   

                                                crew      id  status_code  \
0  [{'profile_path': '/7OGmfDF4VHLLgbjxuEwTj3ga0u...    77.0          NaN   
1  [{'profile_path': '/oTAL0z0vsjipCruxXUsDUIieuh...    98.0          NaN   
2  [{'profile_path': '/qlWi0kufzB7lCq6Jz5zuNE3Kk1...  1359.0          NaN   
3  [{'profile_path': '/isCuZ9PWIOyXzdf3ihodXzjIum...  8358.0          NaN   
4  [{'profile_path': '/fBaZLXX3rBwhSXvtplQEtvW7VS...  7443.0          NaN   

  status_message  
0            NaN  
1            NaN  
2            NaN  
3            NaN  
4            NaN

In [30]:
movie_credits_df['id'].isnull().sum()

37

In [31]:
movie_credits_df.duplicated('id').sum()

7171

In [32]:
movie_credits_df = movie_credits_df[movie_credits_df['id'].isnull()==False]

In [33]:
movie_credits_df.shape

(147470, 5)

In [35]:
movie_credits_df = movie_credits_df.drop_duplicates('id', keep='first')

In [36]:
movie_credits_df.shape

(140335, 5)

In [19]:
#from IPython.display import display
#pd.options.display.max_rows = None
#movie_credits_df.head(90)

In [41]:
start_time = time.time()
movie_cast_df = get_cast(ids_num, movie_credits_df)
print("--- Movie Cast: %s seconds ---" % (time.time() - start_time))
print("")

0             77.0
1             98.0
2           1359.0
3           8358.0
4           7443.0
5            955.0
6            107.0
7           2133.0
8           6282.0
9          40096.0
10           146.0
11         11688.0
12          2024.0
13         10862.0
14         10393.0
15          9532.0
16            71.0
17          1907.0
18         16187.0
19          4247.0
20          4244.0
21          9679.0
22         10473.0
23          6521.0
24          4327.0
25         19457.0
26          2440.0
27          8859.0
28         10562.0
29          2123.0
            ...   
147477    478817.0
147478    475914.0
147479    472053.0
147480    446490.0
147481    453698.0
147482    427535.0
147483    416578.0
147484    476073.0
147485    469100.0
147486    402264.0
147487    459058.0
147488    422598.0
147489    456531.0
147490    461754.0
147491    426642.0
147492    451956.0
147493    408845.0
147494    430472.0
147495    468337.0
147496    474117.0
147497    460644.0
147498    43

KeyboardInterrupt: 

In [42]:
#movie_cast_df.head()